In [1]:
import numpy as np
import pandas as pd
import holoviews as hv
import panel as pn

from colorcet import bmy

pn.extension('tabulator', template='fast')
import hvplot.pandas

## Create intro

In [7]:
instruction = pn.pane.Markdown("""
This dashboard visualizes postal offices and allows exploring the relationships
between their locations and regional characteristics such as transport and telco infrastructures,
complementary public services.<br><br>Box- or lasso-select on each plot to subselect and hit the 
"Clear selection" button to reset.
""", width=600)

panel_logo = pn.pane.PNG(
    'https://panel.holoviz.org/_static/logo_stacked.png',
    link_url='https://panel.holoviz.org', height=95, align='center'
)

event_logo = pn.pane.PNG(
    'https://upload.wikimedia.org/wikipedia/commons/2/2d/Universal_Postal_Union_logo.svg',
    link_url='https://dribdat.hackathon.post/event/3', height=100, align='center'
)

intro = pn.Row(
    event_logo,
    instruction,
    pn.layout.HSpacer(),
    panel_logo,
    sizing_mode='stretch_width'
)

intro

Traceback (most recent call last):
 File "/home/oleg/miniconda3/envs/post/lib/python3.12/site-packages/pyviz_comms/__init__.py", line 340, in _handle_msg
 self._on_msg(msg)
 File "/home/oleg/miniconda3/envs/post/lib/python3.12/site-packages/panel/viewable.py", line 469, in _on_msg
 patch = manager.assemble(msg)
 ^^^^^^^^^^^^^^^^^^^^^
 File "/home/oleg/miniconda3/envs/post/lib/python3.12/site-packages/panel/models/comm_manager.py", line 29, in assemble
 msg_obj = cls(header, msg['metadata'], msg['content'])
 ~~~^^^^^^^^^^^
KeyError: 'content'

Row(sizing_mode='stretch_width')
    [0] PNG(str, align='center', height=100, link_url='https://dribdat.hackathon...)
    [1] Markdown(str, width=600)
    [2] HSpacer()
    [3] PNG(str, align='center', height=95, link_url='https://panel.holoviz.org...)

### Load and cache data

In [6]:
from holoviews.element.tiles import lon_lat_to_easting_northing

@pn.cache
def load_data():
    df = pd.read_csv('data/brazil_geodata_h3_res4.csv')
    df['x'], df['y'] = lon_lat_to_easting_northing(df['X'], df['Y'])
    return df

df = load_data()

df.tail()

X          Y            index  h3_resolution  \
4490 -49.707909 -12.739338  84a8d93ffffffff              4   
4491 -51.197174  -4.880746  84814b1ffffffff              4   
4492 -47.718735  -4.314751  84815b5ffffffff              4   
4493 -49.516998  -1.504511  848044bffffffff              4   
4494 -51.731358 -16.748201  84a8ea9ffffffff              4   

      post_offices_count  postal_bank_count  road_length_km  \
4490                   0                  0     1541.716087   
4491                   0                  0      137.846629   
4492                   0                  1     3178.472903   
4493                   0                  1       59.232572   
4494                   0                  1     1844.737272   

      cell_towers_count  population_count             x             y  
4490                9.0       2440.051854 -5.533459e+06 -1.429968e+06  
4491                NaN        197.881241 -5.699243e+06 -5.439805e+05  
4492              165.0      60535.689792 -5.312025e+06 -4.807705e+05  
4493               50.0      41480.516639 -5.512207e+06 -1.675007e+05  
4494               19.0       4230.374824 -5.758708e+06 -1.891534e+06

### Set up linked selections

In [9]:
ls = hv.link_selections.instance()

def clear_selections(event):
    ls.selection_expr = None

clear_button = pn.widgets.Button(name='Clear selection', align='center')

clear_button.param.watch(clear_selections, 'clicks');

total_area = df.road_length_km.sum()

def count(data):
    selected_area  = np.sum(data['road_length_km'])
    selected_percentage = selected_area / total_area * 100
    return f'## Roads: {len(data)} | Selected: {selected_area:.0f} km ({selected_percentage:.1f}%)</font>'

pn.Row(
    pn.pane.Markdown(pn.bind(count, ls.selection_param(df)), align='center', width=600),
    clear_button
).servable(area='header', title='GeoPostal Impact')

Traceback (most recent call last):
 File "/home/oleg/miniconda3/envs/post/lib/python3.12/site-packages/pyviz_comms/__init__.py", line 340, in _handle_msg
 self._on_msg(msg)
 File "/home/oleg/miniconda3/envs/post/lib/python3.12/site-packages/panel/viewable.py", line 469, in _on_msg
 patch = manager.assemble(msg)
 ^^^^^^^^^^^^^^^^^^^^^
 File "/home/oleg/miniconda3/envs/post/lib/python3.12/site-packages/panel/models/comm_manager.py", line 29, in assemble
 msg_obj = cls(header, msg['metadata'], msg['content'])
 ~~~^^^^^^^^^^^
KeyError: 'content'

Row
    [0] Markdown(str, align='center', width=600)
    [1] Button(align='center', name='Clear selection')

### Create plots

In [18]:
df['post_offices_count_int'] = df['post_offices_count'].fillna(0).astype(int)
df['postal_bank_count_int'] = df['postal_bank_count'].fillna(0).astype(int)


geo = df.hvplot.points(
    'x', 'y', rasterize=True, tools=['hover'], tiles='OSM', cmap=bmy, logz=False, colorbar=True,
    size='post_offices_count',
    xaxis=None, yaxis=False, min_height=400, responsive=True
).opts('Tiles', alpha=0.8)

scatter1 = df.hvplot.scatter(
    'post_offices_count', 'population_count', 
    xlabel='Post offices', ylabel='Population', color='postal_bank_count_int', responsive=True, min_height=400
)

scatter2 = df.hvplot.scatter(
    'road_length_km', 'post_offices_count', 
    xlabel='Road length', ylabel='Post offices', responsive=True, min_height=400
)

scatter3 = df.hvplot.scatter(
    'cell_towers_count', 'post_offices_count', 
    xlabel='Cell towers', ylabel='Post offices', responsive=True, min_height=400
)

hist1 = df.hvplot.hist(
    'post_offices_count_int', xlabel='Number of Post offices',
    fontscale=1.2, responsive=True, min_height=350, fill_color='#85c1e9'
)


hist2 = df.hvplot.hist(
    'postal_bank_count_int', xlabel='Number of Postal banks',
    fontscale=1.2, responsive=True, min_height=350, fill_color='#f1948a'
)

plots = pn.pane.HoloViews(ls(geo + scatter1 + hist1 + hist2 + scatter2 + scatter3).cols(2).opts(sizing_mode='stretch_both'))
plots

Traceback (most recent call last):
 File "/home/oleg/miniconda3/envs/post/lib/python3.12/site-packages/pyviz_comms/__init__.py", line 340, in _handle_msg
 self._on_msg(msg)
 File "/home/oleg/miniconda3/envs/post/lib/python3.12/site-packages/panel/viewable.py", line 469, in _on_msg
 patch = manager.assemble(msg)
 ^^^^^^^^^^^^^^^^^^^^^
 File "/home/oleg/miniconda3/envs/post/lib/python3.12/site-packages/panel/models/comm_manager.py", line 29, in assemble
 msg_obj = cls(header, msg['metadata'], msg['content'])
 ~~~^^^^^^^^^^^
KeyError: 'content'

HoloViews(Layout, sizing_mode='stretch_both')

## Dashboard content


In [13]:
pn.Column(intro, plots, sizing_mode='stretch_both').servable();